In [1]:
import pdfplumber
import re
import requests
from bs4 import BeautifulSoup
import pandas as pd

In [2]:
url = 'http://finance.jxufe.edu.cn/news-list-shuodao-{}.html'
headers ={
        'Accept':'text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3',
        'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/75.0.3770.142 Safari/537.36',     
        'Accept-Encoding': 'gzip, deflate',
        'Accept-Language': 'zh-CN,zh;q=0.9',
        'Cache-Control': 'no-cache',
        'Connection': 'keep-alive',
        'Host': 'finance.jxufe.edu.cn',
        'Pragma': 'no-cache',
        'Referer': 'http://finance.jxufe.edu.cn/news-list-shuodao-1.html',
        'Upgrade-Insecure-Requests': '1'
        }
te_urls = []
for i in range(1,4):
    r = requests.get(url.format(i), headers=headers, timeout=300)
    soup = BeautifulSoup(r.text,'lxml')
    lis = soup.find('div',attrs={'class':'bd_listabc'})
    for j in lis.find_all('li'):
        te_urls.append(j.div.a['href'])

def get_info(url):
    headers ={
        'Accept':'text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3',
        'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/75.0.3770.142 Safari/537.36',     
        'Accept-Encoding': 'gzip, deflate',
        'Accept-Language': 'zh-CN,zh;q=0.9',
        'Cache-Control': 'no-cache',
        'Connection': 'keep-alive',
        'Host': 'finance.jxufe.edu.cn',
        'Pragma': 'no-cache',
        'Referer': 'http://finance.jxufe.edu.cn/news-list-shuodao-1.html',
        'Upgrade-Insecure-Requests': '1'
        }
    r = requests.get(url, headers=headers, timeout=300)
    soup = BeautifulSoup(r.text,'lxml')
    return soup

infos = []
for url in te_urls:
    infos.append(get_info(url))


In [3]:
def te(soup):    
    try:
        lis = soup.find('div',attrs={'class':'ne_main_g'})
        if lis == None:
            lis = soup.find('div',attrs={'class':'ne_main_R'})
        info = []
        dic = {}
        try:
            ss = re.sub('[\xa0\n\u200b\u3000]',' ',lis.text)
            ss = re.sub('\xa0',' ',ss)
            ss = ss.replace(' ','')
            dic['姓名'] = re.search('姓名：.{2,4}性',ss).group(0).split('：')[1][:-1]
            dic['性别'] = re.search('性别：.',ss).group(0).split('：')[1]
            dic['出生年月'] = re.search('出生年月：.{6,8}月',ss).group(0).split('：')[1]
            dic['政治面貌'] = ''
            dic['毕业院校'] = re.search('毕业院校：.{3,10}学',ss).group(0).split('：')[1]
            dic['毕业专业'] = ''
            dic['职务'] = ''
            dic['联系方式'] = re.search('邮箱：.{10,20}m',ss).group(0).split('：')[1]
            return dic
        except:
            for i in lis:
                try:                   
                    info.append(i.text.split('：')[1])
                except:
                    info.append('')
            
            while info[0] == '' :#or info[0][0] == '\\':
                info = info[1:]
            
            dic['姓名'] = info[0]
            dic['性别'] = info[1]
            dic['出生年月'] = info[2]
            dic['政治面貌'] = info[3]
            dic['毕业院校'] = info[4]
            dic['毕业专业'] = info[5]
            dic['职务'] = info[7]
            try:
                dic['联系方式'] = info[8]
            except:
                dic['联系方式'] = ''
            return dic
    except:
        lis = soup.find('td',attrs={'valign':'middle'})
        info = []
        dic = {}
        for i in lis:
            try:
                info.append(i.text.split(':')[1])
            except:
                info.append('')
        dic['姓名'] = info[1]
        dic['性别'] = info[2]
        dic['职位名称'] = info[3]
        dic['毕业院校'] = info[4]
        dic['职务'] = info[5]
        dic['联系方式'] = info[6]
        return dic

teac = []
for x in infos:
    teac.append(te(x))

In [4]:
k = []
v = ['闵晓平']
for i,j in teac[14].items():
    k.append(i)
    v.append(j)
dic = dict(map(lambda x,y:[x,y],k,v))
teac[14] = dic

In [5]:
df = pd.DataFrame(teac[:])
df

姓名     性别                  职位名称  \
0    Badar Nadeem Ashraf   Male   Associate Professor   
1                     曹邓      女                   NaN   
2                    陈春霞      女                   NaN   
3                    陈家洪      男                   NaN   
4                    冯凌秉      男                   NaN   
5                    桂荷发      男                   NaN   
6                    胡少勇      男                   NaN   
7                    胡援成      男                   NaN   
8                    胡志军      男                   NaN   
9                    蒋崇辉      男                   NaN   
10                   李思敏      男                   NaN   
11                   刘金凤      女                   NaN   
12                   刘兴华      男                   NaN   
13                   吕江林      男                   NaN   
14                   闵晓平      男                   NaN   
15                   钱建豪      男                   NaN   
16                    潜力      男                   NaN   
17                    寿晖      男                   NaN   
18                   舒海棠      女                   NaN   
19                   孙爱琳      女                   NaN   
20                    汪洋      男                   NaN   
21                    王辉      男                   NaN   
22                   王清生      男                   NaN   
23                   吴伟军      男                   NaN   
24                    严武      男                   NaN   
25                    杨超      男                   NaN   
26                    杨荣      女                   NaN   
27                   杨玉凤      女                   NaN   
28                   赵玉洁      女                   NaN   
29                   邹朋飞      男                   NaN   
30                   曾鸿志      男                   NaN   
31                   王金佑      男                   NaN   

                                              毕业院校  \
0    Huazhong University of Science and Technology   
1                                           江西财经大学   
2                                           江西财经大学   
3                                           江西财经大学   
4                                         澳大利亚国立大学   
5                                           中国人民大学   
6                                           华东师范大学   
7                                             厦门大学   
8                                           上海财经大学   
9                                           电子科技大学   
10                                                   
11                                                   
12                                            厦门大学   
13                                          中南财经大学   
14                                          上海交通大学   
15                                                   
16                                          西安交通大学   
17                                                   
18                                          江西财经大学   
19                                            浙江大学   
20                                          上海财经大学   
21                                          江西财经大学   
22                                            云南大学   
23                                          江西财经大学   
24                                          江西财经大学   
25                                          西南财经大学   
26                                          江西财经大学   
27                                          江西财经大学   
28                                            复旦大学   
29                                            暨南大学   
30                                            天津大学   
31                                          中国人民大学   

                                         职务                      联系方式  \
0    Teaching/Research/Research supervision        badar@jxufe.edu.cn   
1                                        教授      laotoutou@aliyun.com   
2                                     教授/硕导           new9360@163.com   
3                                     教授/硕导            jxmcjh@126